In [145]:
import os
import tensorflow as tf

# univariate cnn example
from keras.models import Sequential
from keras.layers import Dense
from keras.layers import Flatten
from keras.layers.convolutional import Conv1D
from keras.layers.convolutional import MaxPooling1D
from keras.layers import GlobalAveragePooling1D

import numpy as np
import pandas as pd
# from matplotlib import pyplot as plt

from keras.utils import Sequence
from keras.utils import to_categorical

In [5]:
training_dir = os.listdir('../Pp_Training_SetA/')
list_id = []
for file in training_dir:
    filename = os.fsdecode(file)
    id = filename.lstrip("p").rstrip('.csv')
    list_id.append(id)

In [6]:
df = pd.DataFrame()
for ID in list_id:
    with open(f'../Pp_Training_SetA/p{ID}.csv', 'r') as f:
        df_id = pd.read_csv(f)
        df = df.append(df_id)
df.head()

/var/folders/wq/mnv64xbs77b03n4b7s0w2w3h0000gn/T/ipykernel_14099/174141211.py:5: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(df_id)
/var/folders/wq/mnv64xbs77b03n4b7s0w2w3h0000gn/T/ipykernel_14099/174141211.py:5: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(df_id)
/var/folders/wq/mnv64xbs77b03n4b7s0w2w3h0000gn/T/ipykernel_14099/174141211.py:5: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(df_id)
/var/folders/wq/mnv64xbs77b03n4b7s0w2w3h0000gn/T/ipykernel_14099/174141211.py:5: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(df_id)
/var/folders/wq/mnv64xbs77b03n4b7s0w2w3h0000gn/T

HR     O2Sat      Temp  SBP       MAP  DBP      Resp  BaseExcess  \
0  1.160853  0.353553 -1.870829  0.0  1.532474  0.0  1.207615         0.0   
1  1.160853  0.353553 -1.870829  0.0  1.532474  0.0  1.207615         0.0   
2  1.160853  0.353553 -1.870829  0.0  1.532474  0.0  1.207615         0.0   
3  1.160853  0.353553 -1.870829  0.0  1.532474  0.0  1.207615         0.0   
4  1.160853  0.353553 -1.870829  0.0  1.532474  0.0  1.207615         0.0   

   HCO3  FiO2  ...  WBC  Fibrinogen  Platelets  Age  Gender  Unit1  Unit2  \
0   0.0   0.0  ...  0.0         0.0        0.0  0.0     1.0    1.0    0.0   
1   0.0   0.0  ...  0.0         0.0        0.0  0.0     1.0    1.0    0.0   
2   0.0   0.0  ...  0.0         0.0        0.0  0.0     1.0    1.0    0.0   
3   0.0   0.0  ...  0.0         0.0        0.0  0.0     1.0    1.0    0.0   
4   0.0   0.0  ...  0.0         0.0        0.0  0.0     1.0    1.0    0.0   

   HospAdmTime    ICULOS  SepsisLabel  
0          0.0 -1.428869          1.0  
1          0.0 -1.428869          1.0  
2          0.0 -1.428869          1.0  
3          0.0 -1.428869          1.0  
4          0.0 -1.428869          1.0  

[5 rows x 40 columns]

In [131]:
df = pd.read_csv('data.csv')
df.drop(columns=df.columns[0], axis=1, inplace=True)

In [133]:
X = df.iloc[:,:-1].values
y = df.iloc[:, -1].values

In [134]:
print(X.shape)
print(y.shape)

(989642, 39)
(989642,)


In [135]:
from sklearn.model_selection import train_test_split

#Data splitting
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=42) 
print(X_test.shape)
print(X_train.shape)

(296893, 39)
(692749, 39)


In [ ]:
from keras.preprocessing.sequence import TimeseriesGenerator

train_generator = TimeseriesGenerator(X_train, y_train, length=40, sampling_rate=1, batch_size=40)
test_generator = TimeseriesGenerator(X_test, y_test, length=40, sampling_rate=1, batch_size=40)

train_generator.__next__()

In [148]:
from keras.optimizers import Adam

def define_model(lr, num_classes):
    model = Sequential()
    model.add(Conv1D(filters=32, kernel_size=5, strides=1, padding='same', activation='relu'))
    model.add(MaxPooling1D(pool_size=2))
    model.add(Conv1D(filters=64, kernel_size=5, strides=1, padding='same', activation='relu'))
    model.add(MaxPooling1D(pool_size=2))
    model.add(Conv1D(filters=128, kernel_size=5, strides=1, padding='same', activation='relu'))
    model.add(GlobalAveragePooling1D())
    model.add(Flatten())
    model.add(Dense(128))
    model.add(Dense(num_classes))
    
    opt = Adam(learning_rate=lr)
    model.compile(optimizer=opt, loss='mse', metrics=['accuracy'])
    return model

In [150]:
def evaluate_model(training, testing, max_epochs, learning_rate, momentum, batch_size, model=None, callbacks=[]):
    if model == None:
        model = define_model(learning_rate, momentum)
    history = model.fit(training, epochs=max_epochs, batch_size=batch_size, validation_data=testing, verbose=0, callbacks = callbacks)
    return model, history

In [149]:
model = define_model(lr=0.002,  num_classes=2)

model.fit(train_generator, epochs=10)

Epoch 1/10


2023-01-09 13:01:25.910939: I tensorflow/core/grappler/optimizers/custom_graph_optimizer_registry.cc:114] Plugin optimizer for device_type GPU is enabled.


 4774/17318 [=======>......................] - ETA: 1:49 - loss: 0.0822 - accuracy: 0.5047

KeyboardInterrupt: 